In [5]:
import os, sys
import gitpath
HOME_PATH = gitpath.root()
sys.path.append(HOME_PATH)

import pickle

import numpy as np

# Import pytorch dependencies
import torch
from torch.utils.data import DataLoader

# Import toolkits
from utils.visualization_3D_objects import *

from nn.pointnetae import *
from nn.gf_vae import *

In [6]:
DATASET = 'shapenet'
CATEGORY = 'car'
DATA_PATH = os.path.join(HOME_PATH, "data/preprocessed", DATASET, CATEGORY)
CHECKPOINT_FOLDER = os.path.join(HOME_PATH, "saved_nn")
MODEL_TYPE = "global_feat_VAE_car"
POINTNET_NAME = "PointNetAE_car"

### Import Preprocessed ModelNet40 cars (Run shapenet_preprocessing.ipynb first to get these data)

In [7]:
BATCH_SIZE = 16
global_feat = np.loadtxt("global_feat.csv", delimiter=",", dtype=float)
data_loader = DataLoader(
    global_feat, 
    batch_size=BATCH_SIZE, 
    shuffle=False, 
    num_workers=4,
    drop_last=True
)

### Load saved model

In [8]:
device = 'cuda' if torch.cuda.is_available() else 'cpu'
if device =='cuda':
    print("Run on GPU...")
else:
    print("Run on CPU...")
    
model_test = VAE()
state_dict = torch.load(os.path.join(CHECKPOINT_FOLDER, MODEL_TYPE + '.pth')) # change the path to your own checkpoint file
model_test.cuda()
model_test.load_state_dict(state_dict['state_dict'])
model_test.eval()

print(state_dict['epoch'])

Run on GPU...
340


In [9]:
pointnetae = PointNet_AE(3, 2048)
state_dict = torch.load(os.path.join(CHECKPOINT_FOLDER, POINTNET_NAME + '.pth')) # change the path to your own checkpoint file
pointnetae.cuda()
pointnetae.load_state_dict(state_dict['state_dict'])
pointnetae.eval()

print(state_dict['epoch'])

184


In [40]:
X_sample = pointnetae.decoder(model_test.decoder(torch.randn(12, 128).cuda())).cpu().detach().numpy()
fig = draw3DPoints(X_sample[0], title = "Sampled " + CATEGORY)
fig.show()

In [12]:
def extractGlobalFeatForAllData(data_loader, model_test, device):
    latent_vectors_lst = []
    for batch_idx, (inputs) in enumerate(data_loader):
        # copy inputs to device
        inputs = inputs.float().to(device)
        # compute the output and loss
        outputs, latent_vectors_i = model_test(inputs)
        latent_vectors_lst.append(latent_vectors_i.cpu().detach().numpy())
        
    latent_vectors = np.vstack(latent_vectors_lst)
    return latent_vectors

latent_vectors = extractGlobalFeatForAllData(data_loader, model_test, device)
print(np.mean(np.mean(latent_vectors)), np.mean(np.var(latent_vectors)))

0.0007257525 1.0101138


In [37]:
idx = 17
feature = torch.from_numpy(latent_vectors[idx]).cuda()
feature = feature.view(1, *feature.size())
draw3DPoints(pointnetae.decoder(model_test.decoder(feature)).cpu().detach().numpy()[0])

In [14]:
def interpolate_shape(model_test, pointnetae, global_feat, idx1, idx2, n=20):
    z_1 = global_feat[idx1]
    z_2 = global_feat[idx2]
    
    z = np.stack([z_1 + (z_2 - z_1)*t for t in np.linspace(0, 1, n)])
    z = torch.from_numpy(z).cuda()
    
    interpolate_list = pointnetae.decoder(model_test.decoder(z)).view(n, 1, 3, 2048)
    interpolate_list = interpolate_list.to('cpu').detach().numpy()
    return interpolate_list

In [38]:
interpolate_list = interpolate_shape(model_test, pointnetae, latent_vectors, 12, 17, n=20)

In [39]:
fig = draw3DpointsSlider(interpolate_list, 0, 0)